This notebook serves as an example of how to load and manipulate the [QM9 dataset](https://figshare.com/collections/Quantum_chemistry_structures_and_properties_of_134_kilo_molecules/978904) using a `Dataset` object.

# Imports

In [ ]:
import os
import numpy as np
from ase import Atoms

# Initialize the database

In [ ]:
from colabfit.tools.database import MongoDatabase

client = MongoDatabase('colabfit_rebuild', nprocs=6, drop_database=True)

# Data loading

## Define the properties and reader functions

In [ ]:
client.insert_property_definition({
    'property-id': 'qm9-property',
    'property-title': 'A, B, C, mu, alpha, homo, lumo, gap, r2, zpve, U0, U, H, G, Cv',
    'property-description': 'Geometries minimal in energy, corresponding harmonic frequencies, dipole moments, polarizabilities, along with energies, enthalpies, and free energies of atomization',
    'a':     {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Rotational constant A'},
    'b':     {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Rotational constant B'},
    'c':     {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Rotational constant C'},
    'mu':    {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Dipole moment'},
    'alpha': {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Isotropic polarizability'},
    'homo':  {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Energy of Highest occupied molecular orbital (HOMO)'},
    'lumo':  {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Energy of Lowest occupied molecular orbital (LUMO)'},
    'gap':   {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Gap, difference between LUMO and HOMO'},
    'r2':    {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Electronic spatial extent'},
    'zpve':  {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Zero point vibrational energy'},
    'u0':    {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Internal energy at 0 K'},
    'u':     {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Internal energy at 298.15 K'},
    'h':     {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Enthalpy at 298.15 K'},
    'g':     {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Free energy at 298.15 K'},
    'cv':    {'type': 'float', 'has-unit': True, 'extent': [], 'required': True, 'description': 'Heat capacity at 298.15 K'},
    'smiles-relaxed':    {'type': 'string', 'has-unit': False, 'extent': [], 'required': True, 'description': 'SMILES for relaxed geometry'},
    'inchi-relaxed':     {'type': 'string', 'has-unit': False, 'extent': [], 'required': True, 'description': 'InChI for relaxed geometry'},
})

/home/josh/colabfit/colabfit/tools/database.py:1158: UserWarning: Invalid KIM property-id; Temporarily renaming to tag:@,0000-00-00:property/qm9-property. See https://openkim.org/doc/schema/properties-framework/ for more details.
  warnings.warn(


## Defining a `property_map`

In [4]:
def reader(file_path):
    # A function for returning a list of ASE a
    
    properties_order = [
        'tag', 'index', 'A', 'B', 'C', 'mu', 'alpha', 'homo', 'lumo', 'gap', 'r2', 'zpve', 'U0', 'U', 'H', 'G', 'Cv'
    ]
        
    with open(file_path, 'r') as f:
        lines = [_.strip() for _ in f.readlines()]
        
        na = int(lines[0])
        properties = lines[1].split()
        
        symbols = []
        positions = []
        partial_charges = []
        
        for line in lines[2:2+na]:
            split = line.split()
            split = [_.replace('*^', 'e') for _ in split]  # Python-readable scientific notation
            
            # Line order: symbol, x, y, z, charge
            symbols.append(split[0])
            positions.append(split[1:4])
            partial_charges.append(split[-1])
            
        positions = np.array(positions)
        partial_charges = np.array(partial_charges, dtype=float)
                
        atoms = Atoms(symbols=symbols, positions=positions)
        
        atoms.info['mulliken_partial_charges'] = partial_charges
        
        name = os.path.splitext(os.path.split(file_path)[-1])[0]

        atoms.info['name'] = name
        
        for pname, val in zip(properties_order[2:], properties[2:]):
            atoms.info[pname] = float(val)
            
        frequencies = np.array(lines[-3].split(), dtype=float)
        atoms.info['frequencies'] = frequencies
                
        smiles = lines[-2].split()
        inchi  = lines[-1].split()
        
        atoms.info['SMILES']         = smiles[0]
        atoms.info['SMILES_relaxed'] = smiles[1]
        atoms.info['InChI']          = inchi[0]
        atoms.info['InChI_relaxed']  = inchi[1]
        
        yield atoms

In [5]:
property_map = {
    'qm9-property': [{
        # Property Definition field: {'field': ASE field, 'units': ASE-readable units}
        'a':     {'field': 'A',     'units': 'GHz'},
        'b':     {'field': 'B',     'units': 'GHz'},
        'c':     {'field': 'C',     'units': 'GHz'},
        'mu':    {'field': 'mu',    'units': 'Debye'},
        'alpha': {'field': 'alpha', 'units': 'Bohr*Bohr*Bohr'},
        'homo':  {'field': 'homo',  'units': 'Hartree'},
        'lumo':  {'field': 'lumo',  'units': 'Hartree'},
        'gap':   {'field': 'gap',   'units': 'Hartree'},
        'r2':    {'field': 'r2',    'units': 'Bohr*Bohr'},
        'zpve':  {'field': 'zpve',  'units': 'Hartree'},
        'u0':    {'field': 'U0',    'units': 'Hartree'},
        'u':     {'field': 'U',     'units': 'Hartree'},
        'h':     {'field': 'H',     'units': 'Hartree'},
        'g':     {'field': 'G',     'units': 'Hartree'},
        'cv':    {'field': 'Cv',    'units': 'cal/mol/K'},
        'smiles-relaxed': {'field': 'SMILES_relaxed', 'units': None},
        'inchi-relaxed': {'field': 'SMILES_relaxed',  'units': None},
        
        '_settings': {
            '_method': 'DFT/B3LYP/6-31G(2df,p)',
            '_description': 'QM9 property settings calculation',
            '_files': None,
            '_labels': ['DFT', 'B3LYP', '6-31G(2df,p)'],
        }
    }]
}

## Defining a `property_map`

In [ ]:
property_map = {
    'qm9-property': [{
        # Property Definition field: {'field': ASE field, 'units': ASE-readable units}
        'a':     {'field': 'A',     'units': 'GHz'},
        'b':     {'field': 'B',     'units': 'GHz'},
        'c':     {'field': 'C',     'units': 'GHz'},
        'mu':    {'field': 'mu',    'units': 'Debye'},
        'alpha': {'field': 'alpha', 'units': 'Bohr*Bohr*Bohr'},
        'homo':  {'field': 'homo',  'units': 'Hartree'},
        'lumo':  {'field': 'lumo',  'units': 'Hartree'},
        'gap':   {'field': 'gap',   'units': 'Hartree'},
        'r2':    {'field': 'r2',    'units': 'Bohr*Bohr'},
        'zpve':  {'field': 'zpve',  'units': 'Hartree'},
        'u0':    {'field': 'U0',    'units': 'Hartree'},
        'u':     {'field': 'U',     'units': 'Hartree'},
        'h':     {'field': 'H',     'units': 'Hartree'},
        'g':     {'field': 'G',     'units': 'Hartree'},
        'cv':    {'field': 'Cv',    'units': 'cal/mol/K'},
        'smiles-relaxed': {'field': 'SMILES_relaxed', 'units': None},
        'inchi-relaxed': {'field': 'SMILES_relaxed',  'units': None},
        
        '_settings': {
            '_method': 'DFT/B3LYP/6-31G(2df,p)',
            '_description': 'QM9 property settings calculation',
            '_files': None,
            '_labels': ['DFT', 'B3LYP', '6-31G(2df,p)'],
        }
    }]
}

## Load and insert the data

In [ ]:
from colabfit.tools.database import load_data

images = load_data(
    file_path='/colabfit/data/quantum-machine/qm9',
    file_format='folder',
    name_field='name',  # key in Configuration.info to use as the Configuration name
    elements=['H', 'C', 'N', 'O', 'F'],    # order matters for CFG files, but not others
    default_name='qm9',  # default name with `name_field` not found
    reader=reader,
    glob_string='*.xyz',
    verbose=True
))

Loading file 1/139980: 1it [00:00, 1188.86it/s]
Loading file 2/139980: 1it [00:00, 1466.03it/s]
Loading file 3/139980: 1it [00:00, 1514.74it/s]
Loading file 4/139980: 1it [00:00, 1152.60it/s]
Loading file 5/139980: 1it [00:00, 1365.33it/s]
Loading file 6/139980: 1it [00:00, 1601.49it/s]
Loading file 7/139980: 1it [00:00, 1733.90it/s]
Loading file 8/139980: 1it [00:00, 1387.01it/s]
Loading file 9/139980: 1it [00:00, 1307.04it/s]
Loading file 10/139980: 1it [00:00, 1336.62it/s]
Loading file 11/139980: 1it [00:00, 1399.50it/s]
Loading file 12/139980: 1it [00:00, 1462.45it/s]
Loading file 13/139980: 1it [00:00, 1381.52it/s]
Loading file 14/139980: 1it [00:00, 1539.19it/s]
Loading file 15/139980: 1it [00:00, 1376.99it/s]
Loading file 16/139980: 1it [00:00, 1349.08it/s]
Loading file 17/139980: 1it [00:00, 1578.59it/s]
Loading file 18/139980: 1it [00:00, 1184.83it/s]
Loading file 19/139980: 1it [00:00, 455.56it/s]
Loading file 20/139980: 1it [00:00, 1296.14it/s]
Loading file 21/139980: 1it [0

Loading file 167/139980: 1it [00:00, 1515.83it/s]
Loading file 168/139980: 1it [00:00, 1877.49it/s]
Loading file 169/139980: 1it [00:00, 1931.97it/s]
Loading file 170/139980: 1it [00:00, 1249.05it/s]
Loading file 171/139980: 1it [00:00, 2022.33it/s]
Loading file 172/139980: 1it [00:00, 1948.12it/s]
Loading file 173/139980: 1it [00:00, 1946.31it/s]
Loading file 174/139980: 1it [00:00, 1299.75it/s]
Loading file 175/139980: 1it [00:00, 1419.39it/s]
Loading file 176/139980: 1it [00:00, 1347.78it/s]
Loading file 177/139980: 1it [00:00, 1939.11it/s]
Loading file 178/139980: 1it [00:00, 2019.40it/s]
Loading file 179/139980: 1it [00:00, 1304.20it/s]
Loading file 180/139980: 1it [00:00, 1569.72it/s]
Loading file 181/139980: 1it [00:00, 1477.91it/s]
Loading file 182/139980: 1it [00:00, 1957.21it/s]
Loading file 183/139980: 1it [00:00, 1998.24it/s]
Loading file 184/139980: 1it [00:00, 1774.99it/s]
Loading file 185/139980: 1it [00:00, 1459.40it/s]
Loading file 186/139980: 1it [00:00, 1920.47it/s]


Loading file 331/139980: 1it [00:00, 1402.31it/s]
Loading file 332/139980: 1it [00:00, 1263.73it/s]
Loading file 333/139980: 1it [00:00, 1274.48it/s]
Loading file 334/139980: 1it [00:00, 949.37it/s]
Loading file 335/139980: 1it [00:00, 1047.27it/s]
Loading file 336/139980: 1it [00:00, 1145.05it/s]
Loading file 337/139980: 1it [00:00, 1265.25it/s]
Loading file 338/139980: 1it [00:00, 1165.41it/s]
Loading file 339/139980: 1it [00:00, 1002.70it/s]
Loading file 340/139980: 1it [00:00, 1042.06it/s]
Loading file 341/139980: 1it [00:00, 978.83it/s]
Loading file 342/139980: 1it [00:00, 1136.05it/s]
Loading file 343/139980: 1it [00:00, 1296.94it/s]
Loading file 344/139980: 1it [00:00, 1225.69it/s]
Loading file 345/139980: 1it [00:00, 1038.71it/s]
Loading file 346/139980: 1it [00:00, 1017.79it/s]
Loading file 347/139980: 1it [00:00, 1165.73it/s]
Loading file 348/139980: 1it [00:00, 1192.24it/s]
Loading file 349/139980: 1it [00:00, 1011.41it/s]
Loading file 350/139980: 1it [00:00, 1165.41it/s]
Lo

Loading file 495/139980: 1it [00:00, 1363.56it/s]
Loading file 496/139980: 1it [00:00, 1351.69it/s]
Loading file 497/139980: 1it [00:00, 1829.18it/s]
Loading file 498/139980: 1it [00:00, 1147.55it/s]
Loading file 499/139980: 1it [00:00, 1432.48it/s]
Loading file 500/139980: 1it [00:00, 1862.48it/s]
Loading file 501/139980: 1it [00:00, 1213.98it/s]
Loading file 502/139980: 1it [00:00, 1922.23it/s]
Loading file 503/139980: 1it [00:00, 1033.33it/s]
Loading file 504/139980: 1it [00:00, 1874.97it/s]
Loading file 505/139980: 1it [00:00, 1947.22it/s]
Loading file 506/139980: 1it [00:00, 1941.81it/s]
Loading file 507/139980: 1it [00:00, 1346.05it/s]
Loading file 508/139980: 1it [00:00, 1964.55it/s]
Loading file 509/139980: 1it [00:00, 1943.61it/s]
Loading file 510/139980: 1it [00:00, 1115.80it/s]
Loading file 511/139980: 1it [00:00, 1114.91it/s]
Loading file 512/139980: 1it [00:00, 1816.50it/s]
Loading file 513/139980: 1it [00:00, 1826.79it/s]
Loading file 514/139980: 1it [00:00, 1797.05it/s]


Loading file 658/139980: 1it [00:00, 1843.65it/s]
Loading file 659/139980: 1it [00:00, 1903.91it/s]
Loading file 660/139980: 1it [00:00, 1942.71it/s]
Loading file 661/139980: 1it [00:00, 1832.37it/s]
Loading file 662/139980: 1it [00:00, 1760.83it/s]
Loading file 663/139980: 1it [00:00, 1883.39it/s]
Loading file 664/139980: 1it [00:00, 1861.65it/s]
Loading file 665/139980: 1it [00:00, 1367.11it/s]
Loading file 666/139980: 1it [00:00, 1304.60it/s]
Loading file 667/139980: 1it [00:00, 1289.76it/s]
Loading file 668/139980: 1it [00:00, 1919.59it/s]
Loading file 669/139980: 1it [00:00, 1907.37it/s]
Loading file 670/139980: 1it [00:00, 1867.46it/s]
Loading file 671/139980: 1it [00:00, 1844.46it/s]
Loading file 672/139980: 1it [00:00, 1223.90it/s]
Loading file 673/139980: 1it [00:00, 1081.56it/s]
Loading file 674/139980: 1it [00:00, 1518.57it/s]
Loading file 675/139980: 1it [00:00, 946.15it/s]
Loading file 676/139980: 1it [00:00, 1120.87it/s]
Loading file 677/139980: 1it [00:00, 1475.83it/s]
L

...

Loading file 100936/139980: 1it [00:00, 14.40it/s]
Loading file 100937/139980: 1it [00:00, 69.37it/s]
Loading file 100938/139980: 1it [00:00, 35.79it/s]
Loading file 100939/139980: 1it [00:00, 104.45it/s]
Loading file 100940/139980: 1it [00:00, 35.09it/s]
Loading file 100941/139980: 1it [00:00, 113.19it/s]
Loading file 100942/139980: 1it [00:00, 16.48it/s]
Loading file 100943/139980: 1it [00:00, 193.59it/s]
Loading file 100944/139980: 1it [00:00,  2.06it/s]
Loading file 100945/139980: 1it [00:00, 70.89it/s]
Loading file 100946/139980: 1it [00:00, 23.83it/s]
Loading file 100947/139980: 1it [00:00, 56.71it/s]
Loading file 100948/139980: 1it [00:00, 41.35it/s]
Loading file 100949/139980: 1it [00:00, 320.22it/s]
Loading file 100950/139980: 1it [00:00, 49.81it/s]
Loading file 100951/139980: 1it [00:00, 39.94it/s]
Loading file 100952/139980: 1it [00:00, 59.81it/s]
Loading file 100953/139980: 1it [00:00, 24.69it/s]
Loading file 100954/139980: 1it [00:00, 353.15it/s]
Loading file 100955/139980

Loading file 101095/139980: 1it [00:00, 68.34it/s]
Loading file 101096/139980: 1it [00:00, 51.13it/s]
Loading file 101097/139980: 1it [00:00, 421.58it/s]
Loading file 101098/139980: 1it [00:00, 30.76it/s]
Loading file 101099/139980: 1it [00:00, 390.82it/s]
Loading file 101100/139980: 1it [00:00, 85.61it/s]
Loading file 101101/139980: 1it [00:00, 166.45it/s]
Loading file 101102/139980: 1it [00:00, 67.53it/s]
Loading file 101103/139980: 1it [00:00, 67.00it/s]
Loading file 101104/139980: 1it [00:00, 370.98it/s]
Loading file 101105/139980: 1it [00:00, 420.99it/s]
Loading file 101106/139980: 1it [00:00, 50.21it/s]
Loading file 101107/139980: 1it [00:00, 30.77it/s]
Loading file 101108/139980: 1it [00:00, 44.11it/s]
Loading file 101109/139980: 1it [00:00, 377.56it/s]
Loading file 101110/139980: 1it [00:00, 410.96it/s]
Loading file 101111/139980: 1it [00:00, 38.76it/s]
Loading file 101112/139980: 1it [00:00, 374.29it/s]
Loading file 101113/139980: 1it [00:00, 132.34it/s]
Loading file 101114/13

Loading file 101254/139980: 1it [00:00, 262.09it/s]
Loading file 101255/139980: 1it [00:00, 26.88it/s]
Loading file 101256/139980: 1it [00:00, 106.20it/s]
Loading file 101257/139980: 1it [00:00, 28.36it/s]
Loading file 101258/139980: 1it [00:00, 98.90it/s]
Loading file 101259/139980: 1it [00:00, 442.72it/s]
Loading file 101260/139980: 1it [00:00, 26.10it/s]
Loading file 101261/139980: 1it [00:00, 83.86it/s]
Loading file 101262/139980: 1it [00:00, 42.63it/s]
Loading file 101263/139980: 1it [00:00, 481.11it/s]
Loading file 101264/139980: 1it [00:00, 121.28it/s]
Loading file 101265/139980: 1it [00:00, 423.75it/s]
Loading file 101266/139980: 1it [00:00, 385.79it/s]
Loading file 101267/139980: 1it [00:00, 171.06it/s]
Loading file 101268/139980: 1it [00:00, 90.62it/s]
Loading file 101269/139980: 1it [00:00, 50.40it/s]
Loading file 101270/139980: 1it [00:00, 43.04it/s]
Loading file 101271/139980: 1it [00:00, 59.10it/s]
Loading file 101272/139980: 1it [00:00, 377.19it/s]
Loading file 101273/13

Loading file 101413/139980: 1it [00:00, 315.08it/s]
Loading file 101414/139980: 1it [00:00, 66.79it/s]
Loading file 101415/139980: 1it [00:00, 416.85it/s]
Loading file 101416/139980: 1it [00:00, 19.80it/s]
Loading file 101417/139980: 1it [00:00, 47.35it/s]
Loading file 101418/139980: 1it [00:00, 426.16it/s]
Loading file 101419/139980: 1it [00:00,  7.48it/s]
Loading file 101420/139980: 1it [00:00, 57.41it/s]
Loading file 101421/139980: 1it [00:00, 424.74it/s]
Loading file 101422/139980: 1it [00:00, 72.37it/s]
Loading file 101423/139980: 1it [00:00, 29.80it/s]
Loading file 101424/139980: 1it [00:00, 35.30it/s]
Loading file 101425/139980: 1it [00:00, 99.95it/s]
Loading file 101426/139980: 1it [00:00, 362.92it/s]
Loading file 101427/139980: 1it [00:00, 450.37it/s]
Loading file 101428/139980: 1it [00:00,  5.42it/s]
Loading file 101429/139980: 1it [00:00, 71.01it/s]
Loading file 101430/139980: 1it [00:00, 70.82it/s]
Loading file 101431/139980: 1it [00:00, 65.14it/s]
Loading file 101432/13998

Loading file 101572/139980: 1it [00:00, 57.51it/s]
Loading file 101573/139980: 1it [00:00, 51.78it/s]
Loading file 101574/139980: 1it [00:00, 320.10it/s]
Loading file 101575/139980: 1it [00:00,  7.46it/s]
Loading file 101576/139980: 1it [00:00, 66.73it/s]
Loading file 101577/139980: 1it [00:00, 353.83it/s]
Loading file 101578/139980: 1it [00:00, 317.51it/s]
Loading file 101579/139980: 1it [00:00, 44.89it/s]
Loading file 101580/139980: 1it [00:00, 22.29it/s]
Loading file 101581/139980: 1it [00:00, 33.13it/s]
Loading file 101582/139980: 1it [00:00, 56.57it/s]
Loading file 101583/139980: 1it [00:00, 373.92it/s]
Loading file 101584/139980: 1it [00:00, 49.50it/s]
Loading file 101585/139980: 1it [00:00, 90.25it/s]
Loading file 101586/139980: 1it [00:00, 21.47it/s]
Loading file 101587/139980: 1it [00:00, 30.67it/s]
Loading file 101588/139980: 1it [00:00, 58.81it/s]
Loading file 101589/139980: 1it [00:00, 48.88it/s]
Loading file 101590/139980: 1it [00:00, 36.52it/s]
Loading file 101591/139980:

In [ ]:
from colabfit.tools.property_settings import PropertySettings

ids = list(client.insert_data(
    images,
    property_map=property_map,
    generator=True,
    verbose=True
))

Preparing to add configurations to Database: 41699it [02:07, 32.26it/s] 

In [ ]:
len(ids)

# Defining `ConfigurationSet`s

In [ ]:
co_ids1 = client.get_data('configurations', fields='_id', query={'names': {'$regex': 'dsC7O2H10nsd'}}, ravel=True).tolist()
co_ids2 = client.get_data('configurations', fields='_id', query={'names': {'$regex': 'dsgdb9nsd'}}, ravel=True).tolist()

print('Configuration set 1', '(dsC7O2H10nsd):'.rjust(15), f'{len(co_ids1)}'.rjust(7))
print('Configuration set 2', '(dsgdb9nsd):'.rjust(15), f'{len(co_ids2)}'.rjust(7))

In [ ]:
cs_id1 = client.insert_configuration_set(
    co_ids1,
    description='Isomers of C7O2H10',
    verbose=True
)
cs_id1

In [ ]:
cs_id2 = client.insert_configuration_set(
    co_ids2,
    description='The subset of all 133,885 species with up to '\
    'nine heavy atoms (CONF) out of the GDB-17 chemical universe '\
    'of 166 billion organic molecules',
    verbose=True
)
cs_id2

In [ ]:
cs1 = client.get_configuration_set(cs_id1)['configuration_set']

print(cs1.description)

for k,v in cs1.aggregated_info.items():
    print(k, v)

In [ ]:
cs2 = client.get_configuration_set(cs_id2)['configuration_set']

print(cs2.description)

for k,v in cs2.aggregated_info.items():
    print(k, v)

# Defining `Dataset`s

In [ ]:
all_co_ids, all_pr_ids = list(zip(*ids))
len(all_pr_ids)

In [ ]:
ds_id = client.insert_dataset(
    cs_ids=[cs_id1, cs_id2],
    pr_ids=all_pr_ids,
    name='QM9',
    authors=['Raghunathan Ramakrishnan', 'Pavlo Dral', 'Matthias Rupp', 'O. Anatole von Lilienfeld'],
    links=[
        'https://www.nature.com/articles/sdata201422',
        'https://figshare.com/collections/Quantum_chemistry_structures_and_properties_of_134_kilo_molecules/978904'
    ],
    description="The QM9 dataset, split into the GDB-9 molecules and the C7O2H10 isomers",
    resync=True,
    verbose=True,
)
ds_id

In [ ]:
ds_id = '9615499379302979156'
dataset = client.get_dataset(ds_id, resync=True, verbose=True)['dataset']

for k,v in dataset.aggregated_info.items():
    print(k,v)

# Next up: exploring a dataset

In [ ]:
client.get_statistics(
    ['qm9-property.a', 'qm9-property.b', 'qm9-property.c'],
    ids=dataset.property_ids,
    verbose=True
)

In [ ]:
fig = client.plot_histograms(
    ['qm9-property.a', 'qm9-property.b', 'qm9-property.c',],
    ids=dataset.property_ids
)

In [ ]:
client.dataset_to_markdown(
    ds_id=ds_id,
    base_folder='/colabfit/markdown/'+dataset.name,
    html_file_name='README.md',
    data_format='mongo',
    data_file_name=None,
    histogram_fields=[
        'qm9-property.a',
        'qm9-property.b',
        'qm9-property.c',
        'qm9-property.mu',
        'qm9-property.alpha',
        'qm9-property.homo',
        'qm9-property.lumo',
        'qm9-property.gap',
        'qm9-property.r2',
        'qm9-property.zpve',
        'qm9-property.u0',
        'qm9-property.u',
        'qm9-property.h',
        'qm9-property.g',
        'qm9-property.cv',
#         'qm9-property.smiles-relaxed',
#         'qm9-property.inchi-relaxed'
    ],
    yscale='log'
)

In [ ]:
clean_config_sets, clean_property_ids = client.filter_on_properties(
    ds_id=ds_id,
    filter_fxn=lambda x: (x['qm9-property']['a']['source-value'] < 20) and x['qm9-property']['b']['source-value'] < 10,
    fields=['qm9-property.a.source-value', 'qm9-property.b.source-value'],
    verbose=True
)

In [ ]:
new_cs_ids = []
for cs in clean_config_sets:
    new_cs_ids.append(client.insert_configuration_set(cs.configuration_ids, cs.description, verbose=True))
    
print(new_cs_ids)

In [ ]:
ds_id_clean = client.insert_dataset(
    cs_ids=new_cs_ids,
    pr_ids=clean_property_ids,
    name='QM9_filtered',
    authors=dataset.authors,
    links=[
        'https://www.nature.com/articles/sdata201422',
        'https://figshare.com/collections/Quantum_chemistry_structures_and_properties_of_134_kilo_molecules/978904'
    ],
    description="The QM9 dataset, filtered by removing values with a>=20 or b>=10",
    resync=True,
    verbose=True,
)
ds_id_clean

In [ ]:
ds_id_clean = '3071118515767946833'

clean_ds = client.get_dataset(ds_id_clean)['dataset']
len(clean_ds.property_ids)

In [ ]:
fig = client.plot_histograms(
    ['qm9-property.a', 'qm9-property.b', 'qm9-property.c'],
    ids=clean_ds.property_ids,
    verbose=True
)

In [ ]:
client.dataset_to_markdown(
    ds_id=ds_id_clean,
    base_folder='/colabfit/markdown/'+clean_ds.name,
    html_file_name='README.md',
    data_format='mongo',
    data_file_name=None,
    histogram_fields=[
        'qm9-property.a',
        'qm9-property.b',
        'qm9-property.c',
        'qm9-property.mu',
        'qm9-property.alpha',
        'qm9-property.homo',
        'qm9-property.lumo',
        'qm9-property.gap',
        'qm9-property.r2',
        'qm9-property.zpve',
        'qm9-property.u0',
        'qm9-property.u',
        'qm9-property.h',
        'qm9-property.g',
        'qm9-property.cv',
#         'qm9-property.smiles-relaxed',
#         'qm9-property.inchi-relaxed'
    ],
    yscale='log'
)